<a href="https://colab.research.google.com/github/darshanparamane/walmart_sales_pred/blob/main/walmart_sa_es.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# Jovian Commit Essentials
# Please retain and execute this cell without modifying the contents for `jovian.commit` to work
!pip install jovian --upgrade -q
import jovian
jovian.set_project('walmart-sa-es')
jovian.set_colab_id('1_kq9jVSPW5z6VdRiiugqsDcLE2FknZ_I')

# walmart-sa-es

Use the "Run" button to execute the code.

In [2]:
!pip install jovian --upgrade --quiet

LIBRARIES

In [5]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objs as go
import plotly.figure_factory as ff
from plotly.offline import iplot, init_notebook_mode
init_notebook_mode()

from sklearn import model_selection
from sklearn import metrics, ensemble, linear_model
import xgboost as xgb
import lightgbm as lgb
from sklearn.experimental import enable_hist_gradient_boosting
from sklearn.ensemble import HistGradientBoostingRegressor
import warnings
warnings.filterwarnings('ignore') 
%matplotlib inline

/usr/local/lib/python3.7/dist-packages/sklearn/experimental/enable_hist_gradient_boosting.py:17: UserWarning:

Since version 1.0, it is not needed to import enable_hist_gradient_boosting anymore. HistGradientBoostingClassifier and HistGradientBoostingRegressor are now stable and can be normally imported from sklearn.ensemble.



DATA **LOADING**

In [6]:
!pip install opendatasets scikit-learn jovian --quiet --upgrade

In [7]:
import os
import opendatasets as od
import pandas as pd
pd.set_option("display.max_columns", 120)
pd.set_option("display.max_rows", 120)

In [8]:
od.download('https://www.kaggle.com/competitions/walmart-recruiting-store-sales-forecasting/data')

Skipping, found downloaded files in "./walmart-recruiting-store-sales-forecasting" (use force=True to force download)


In [9]:
os.listdir('walmart-recruiting-store-sales-forecasting')

['train.csv.zip',
 'stores.csv',
 'test.csv.zip',
 'sampleSubmission.csv.zip',
 'features.csv.zip']

In [10]:
features=pd.read_csv('walmart-recruiting-store-sales-forecasting/features.csv.zip')
test=pd.read_csv('walmart-recruiting-store-sales-forecasting/test.csv.zip')
train=pd.read_csv('walmart-recruiting-store-sales-forecasting/train.csv.zip')
stores=pd.read_csv('walmart-recruiting-store-sales-forecasting/stores.csv')
sample_submission = pd.read_csv('walmart-recruiting-store-sales-forecasting/sampleSubmission.csv.zip')

In [11]:
feature_store = features.merge(stores, how='inner', on = "Store")

In [12]:
train_df = train.merge(feature_store, how='inner', on = ['Store','Date','IsHoliday']).sort_values(by=['Store','Dept','Date']).reset_index(drop=True)

In [13]:
test_df = test.merge(feature_store, how='inner', on = ['Store','Date','IsHoliday']).sort_values(by = ['Store','Dept','Date']).reset_index(drop=True)

EXPLORATORY DATA ANALYSIS

The EDA is one of the most important parts of the process, because will gives you an idea about the relationship of the features, your distribution, and so on.


In [14]:
train_df.describe().T.style.bar(subset=['mean'], color='#205ff2')\
                            .background_gradient(subset=['std'], cmap='Reds')\
                            .background_gradient(subset=['50%'], cmap='coolwarm')

In [15]:
feature_store = features.merge(stores, how='inner', on = "Store")

# Converting date column to datetime 
feature_store['Date'] = pd.to_datetime(feature_store['Date'])
train['Date'] = pd.to_datetime(train['Date'])
test['Date'] = pd.to_datetime(test['Date'])

# Adding some basic datetime features
feature_store['Day'] = feature_store['Date'].dt.day
feature_store['Week'] = feature_store['Date'].dt.week
feature_store['Month'] = feature_store['Date'].dt.month
feature_store['Year'] = feature_store['Date'].dt.year

In [16]:
train_df = train.merge(feature_store, how='inner', on = ['Store','Date','IsHoliday']).sort_values(by = ['Store','Dept','Date']).reset_index(drop=True)

In [17]:
test_df = test.merge(feature_store, how='inner', on = ['Store','Date','IsHoliday']).sort_values(by = ['Store','Dept','Date']).reset_index(drop=True)

In [18]:
df_weeks = train_df.groupby('Week').sum()

In [19]:
df_weeks

Store    Dept  Weekly_Sales  IsHoliday  Temperature  Fuel_Price  \
Week                                                                     
1     130899  260501  8.773121e+07          0    222343.25   18872.529   
2     131036  260045  8.269676e+07          0    204005.74   19098.337   
3     130031  259381  8.273564e+07          0    222547.92   19167.202   
4     129971  259111  7.943483e+07          0    221326.56   19229.283   
5     195904  392036  1.419895e+08          0    317172.19   27489.729   
6     196850  394786  1.456823e+08       8895    308692.32   27771.111   
7     197602  396508  1.471902e+08          0    362493.21   28048.496   
8     195853  390108  1.338659e+08          0    369896.71   28063.010   
9     197097  393893  1.407131e+08          0    388853.51   29131.976   
10    196989  393404  1.380332e+08          0    416255.07   29839.192   
11    196201  390381  1.367628e+08          0    461093.42   30174.510   
12    196360  390003  1.320040e+08          0    460038.46   30288.098   
13    196715  390112  1.391557e+08          0    465264.84   30602.032   
14    196812  391310  1.467551e+08          0    501300.16   31086.190   
15    196808  392212  1.367863e+08          0    508245.48   31600.352   
16    196773  391121  1.384837e+08          0    520250.05   31705.759   
17    195943  388947  1.309520e+08          0    532981.19   31634.951   
18    196663  393242  1.424894e+08          0    547803.31   31981.274   
19    196957  393186  1.377021e+08          0    557906.60   31956.617   
20    195559  389258  1.359906e+08          0    571306.22   31538.139   
21    195312  389008  1.409434e+08          0    617033.43   30966.229   
22    194741  388805  1.472422e+08          0    639721.02   30427.928   
23    195540  389913  1.451475e+08          0    643886.47   30153.947   
24    196214  392639  1.434817e+08          0    652790.54   29965.073   
25    195910  391388  1.401614e+08          0    679584.79   29711.159   
26    195394  388868  1.430931e+08          0    686714.37   29263.516   
27    195598  390962  1.470118e+08          0    697458.42   28976.137   
28    195426  390090  1.378596e+08          0    696714.14   29047.241   
29    195557  390257  1.362228e+08          0    706420.44   29287.175   
30    195140  389019  1.324108e+08          0    698956.30   29511.963   
31    196051  390930  1.437064e+08          0    705613.56   29674.594   
32    195574  389572  1.401174e+08          0    703565.60   29801.041   
33    195949  391103  1.413328e+08          0    694943.23   29909.602   
34    195786  391137  1.407740e+08          0    675165.38   29878.996   
35    196353  391745  1.397305e+08          0    683666.34   29962.941   
36    196950  392037  1.407277e+08       8861    657188.55   30285.692   
37    196702  389877  1.311007e+08          0    621898.91   30293.814   
38    196505  389851  1.284312e+08          0    607417.90   30360.496   
39    196562  389792  1.281706e+08          0    618877.24   30018.942   
40    197015  392476  1.398813e+08          0    559526.19   29971.123   
41    196545  392743  1.336528e+08          0    533518.31   30241.820   
42    196083  390110  1.340080e+08          0    527231.83   30274.936   
43    196606  390806  1.350028e+08          0    516608.10   30091.173   
44    130444  259258  9.443753e+07          0    295890.02   18741.228   
45    130770  260063  9.459903e+07          0    290569.71   18761.020   
46    130237  258792  9.156456e+07          0    292393.18   18823.215   
47    132081  265174  1.324146e+08       5959    287458.61   18954.198   
48    131849  263243  9.929958e+07          0    258056.84   18698.409   
49    132163  264616  1.112279e+08          0    227502.65   18906.263   
50    132570  265152  1.219065e+08          0    239417.94   18953.601   
51    132580  266031  1.579297e+08          0    237788.26   18905.147   
52    131854  263820  8.647498e+07       5946    218811.58   18810.547   

         M

Sales analysis

In [20]:
import plotly.io as pio
pio.renderers.default = "colab"

In [21]:
palette = px.colors.qualitative.Safe

In [22]:
px.line( data_frame = df_weeks, x = df_weeks.index, y = 'Weekly_Sales', 
        labels = {'Weekly_Sales' : 'Weekly Sales', 'x' : 'Weeks' }, 
        title = 'Sales over weeks', color_discrete_sequence=palette)

Insights:
The sales across the year are quite stable, with a plunge around the week 42, and a recovery for the holidays. 

**Markdowns relationship with sales**

[jovian] Detected Colab notebook...
[jovian] Please enter your API key ( from https://jovian.ai/ ):
API KEY: ··········
API KEY: 


Abort: ignored

In [24]:
fig = go.Figure()
fig.add_trace(go.Scatter( x = df_weeks.index, y = df_weeks['MarkDown1'], name = 'MarkDown1', mode = 'lines') )
fig.add_trace(go.Scatter( x = df_weeks.index, y = df_weeks['MarkDown2'], name = 'MarkDown2', mode = 'lines') )
fig.add_trace(go.Scatter( x = df_weeks.index, y = df_weeks['MarkDown3'], name = 'MarkDown3', mode = 'lines') )
fig.add_trace(go.Scatter( x = df_weeks.index, y = df_weeks['MarkDown4'], name = 'MarkDown4', mode = 'lines') )
fig.add_trace(go.Scatter( x = df_weeks.index, y = df_weeks['MarkDown5'], name = 'MarkDown5', mode = 'lines') )
fig.add_trace(go.Scatter( x = df_weeks.index, y = df_weeks['Weekly_Sales'], name = 'Weekly Sales', mode = 'lines') )
fig.update_layout(title = "Sales vs Markdown's", xaxis_title = 'Weeks')

**Mean sales comparassion across the years**

In [25]:
weekly_sales = train_df.groupby(['Year','Week'], as_index = False).agg({'Weekly_Sales': ['mean', 'median']})
weekly_sales2010 = train_df.loc[train_df['Year']==2010].groupby(['Week']).agg({'Weekly_Sales': ['mean', 'median']})
weekly_sales2011 = train_df.loc[train_df['Year']==2011].groupby(['Week']).agg({'Weekly_Sales': ['mean', 'median']})
weekly_sales2012 = train_df.loc[train_df['Year']==2012].groupby(['Week']).agg({'Weekly_Sales': ['mean', 'median']})

In [26]:
fig = go.Figure()
fig.add_trace(go.Scatter( x = weekly_sales2010['Weekly_Sales']['mean'].index, y = weekly_sales2010['Weekly_Sales']['mean'], name = 'Mean Sales 2010', mode = 'lines') )
fig.add_trace(go.Scatter( x = weekly_sales2011['Weekly_Sales']['mean'].index, y = weekly_sales2011['Weekly_Sales']['mean'], name = 'Mean Sales 2011', mode = 'lines') )
fig.add_trace(go.Scatter( x = weekly_sales2012['Weekly_Sales']['mean'].index, y = weekly_sales2012['Weekly_Sales']['mean'], name = 'Mean Sales 2012', mode = 'lines') )
fig.add_annotation(text="Thanskgiving", x=47, y=25000, showarrow=False)
fig.add_annotation(text="Christmas", x=51, y=29000, showarrow=False)
fig.update_layout(title = 'Sales 2010, 2011, 2012', xaxis_title = 'Weeks')

**Insights:
There's a clear pattern about the sales across the years, by Thanksgiving and Christmas the sales rise up by a huge margin.**

In [27]:
# Converting the temperature to celsius for a better interpretation
train_df['Temperature'] = train_df['Temperature'].apply(lambda x :  (x - 32) / 1.8)
train_df['Temperature'] = train_df['Temperature'].apply(lambda x :  (x - 32) / 1.8)

In [28]:
train_plt = train_df.sample(frac=0.10)

In [29]:
import plotly.io as pio
pio.renderers.default = "colab"
px.violin(train_plt, x='Temperature', y ='Weekly_Sales', color='IsHoliday', 
         color_discrete_sequence=palette)

Insights:
There is a pattern between the coldness and the sales, obviously related to the fact that the USA is in the northern hemisphere, and it is a country where a large part of it experiences cold temperatures for this time.

In [30]:
px.violin(train_plt, x='Fuel_Price', y ='Weekly_Sales', color='IsHoliday', 
           title='Fuel price and sales by holiday',color_discrete_sequence=palette)

There is not a clear pattern but lower the fuel prices more the sales

In [31]:
px.violin(train_plt, x='CPI', y ='Weekly_Sales', color='IsHoliday', 
           title='CPI and sales by holiday',color_discrete_sequence=palette)

**Here there is not a very clear pattern either, you can see that there are 3 groups, but in all of them you have sales, despite the fact that the CPI is higher.**

In [32]:
px.violin(train_plt, x='Unemployment', y ='Weekly_Sales', color='IsHoliday', 
           title='Unemployment rate and sales by holiday',color_discrete_sequence=palette)

**Insights:
In relation to unemployment, it can be seen that the lower the value, higher the sales, it makes sense.**

In [33]:
sizes= train_plt.groupby('Size').mean()
px.line(sizes, x = sizes.index, y = sizes.Weekly_Sales, 
        title='Store size and sales',color_discrete_sequence=palette)

Insights:
Size is an important factor when it comes to sales, as you can see here.

In [34]:
store_type = pd.concat([stores['Type'], stores['Size']], axis=1)
px.box(store_type, x='Type', y='Size', color='Type', 
       title='Store size and Store type',color_discrete_sequence=palette)

Insights:
Within size we can see that there are 3 types of stores, the A are the most present.

In [35]:
store_sale = pd.concat([stores['Type'], train_df['Weekly_Sales']], axis=1)
px.box(store_sale.dropna(), x='Type', y='Weekly_Sales', color='Type', 
       title='Store type and sales',color_discrete_sequence=palette)

**Insights:
In relation to the type of store we can see that although the C are the smallest ones, they are those that have the highest median sales.**

In [36]:
depts= train_plt.groupby('Dept').mean().sort_values(by='Weekly_Sales', ascending='False')
bar=px.bar(depts, x = depts.index, y =  depts.Weekly_Sales, 
           title='Departament and sales',color=depts.Weekly_Sales)
bar.update_layout(barmode='group', xaxis={'categoryorder':'total descending'})

Insights:
Some departaments contributes to sales more than others.

# ** Heatmap and correlation between features**

In [37]:
corr = train_df.corr()
mask = np.triu(np.ones_like(corr, dtype=bool))
df_mask = corr.mask(mask).round(2)

fig = ff.create_annotated_heatmap(z=df_mask.to_numpy(), 
                                  x=df_mask.columns.tolist(),
                                  y=df_mask.columns.tolist(),
                                  colorscale=px.colors.diverging.RdBu,
                                  hoverinfo="none", 
                                  showscale=True, ygap=1, xgap=1
                                 )

fig.update_xaxes(side="bottom")

fig.update_layout(
    title_text='Heatmap', 
    title_x=0.5, 
    width=1000, 
    height=1000,
    xaxis_showgrid=False,
    yaxis_showgrid=False,
    xaxis_zeroline=False,
    yaxis_zeroline=False,
    yaxis_autorange='reversed',
    template='plotly_white'
)
for i in range(len(fig.layout.annotations)):
    if fig.layout.annotations[i].text == 'nan':
        fig.layout.annotations[i].text = ""

fig.show()

In [38]:
weekly_sales_corr = train_df.corr().iloc[2,:]
corr_df = pd.DataFrame(data = weekly_sales_corr, index = weekly_sales_corr.index ).sort_values (by = 'Weekly_Sales', ascending = False)
corr_df = corr_df.iloc[1:]
bar = px.bar(corr_df, x = corr_df.index, y = 'Weekly_Sales', color=corr_df.index, labels={'index':'Featues'},
             title='Feature correlation with sales',color_discrete_sequence=palette)
bar.update_traces(showlegend=False)

# Feature Engineering

In [39]:
data_train = train_df.copy()
data_test = test_df.copy()

**Since Thanksgiving and Christmas are the most importarnt holidays, I'm going to try some feature engineering on this features, and also Superbowl and Laborday.**

In [40]:
data_train['Days_to_Thansksgiving'] = (pd.to_datetime(train_df["Year"].astype(str)+"-11-24", format="%Y-%m-%d") - pd.to_datetime(train_df["Date"], format="%Y-%m-%d")).dt.days.astype(int)
data_train['Days_to_Christmas'] = (pd.to_datetime(train_df["Year"].astype(str)+"-12-24", format="%Y-%m-%d") - pd.to_datetime(train_df["Date"], format="%Y-%m-%d")).dt.days.astype(int)

In [41]:

data_test['Days_to_Thansksgiving'] = (pd.to_datetime(test_df["Year"].astype(str)+"-11-24", format="%Y-%m-%d") - pd.to_datetime(test_df["Date"], format="%Y-%m-%d")).dt.days.astype(int)
data_test['Days_to_Christmas'] = (pd.to_datetime(test_df["Year"].astype(str)+"-12-24", format="%Y-%m-%d") - pd.to_datetime(test_df["Date"], format="%Y-%m-%d")).dt.days.astype(int)

In [42]:
data_train['SuperBowlWeek'] = train_df['Week'].apply(lambda x: 1 if x == 6 else 0)
data_train['LaborDay'] = train_df['Week'].apply(lambda x: 1 if x == 36 else 0)
data_train['Tranksgiving'] = train_df['Week'].apply(lambda x: 1 if x == 47 else 0)
data_train['Christmas'] = train_df['Week'].apply(lambda x: 1 if x == 52 else 0)

In [43]:
data_train['MarkdownsSum'] = train_df['MarkDown1'] + train_df['MarkDown2'] + train_df['MarkDown3'] + train_df['MarkDown4'] + train_df['MarkDown5'] 

In [44]:
data_test['MarkdownsSum'] = test_df['MarkDown1'] + test_df['MarkDown2'] + test_df['MarkDown3'] + test_df['MarkDown4'] + test_df['MarkDown5']

# PREPOCESSING
**Filling missing values**

In [47]:
data_train.isna().sum()[data_train.isna().sum() > 0].sort_values(ascending=False)

MarkdownsSum    324514
MarkDown2       310322
MarkDown4       286603
MarkDown3       284479
MarkDown1       270889
MarkDown5       270138
dtype: int64

In [48]:
data_test.isna().sum()[data_test.isna().sum() > 0].sort_values(ascending=False)

CPI             38162
Unemployment    38162
MarkdownsSum    37457
MarkDown2       28627
MarkDown4       12888
MarkDown3        9829
MarkDown1         149
dtype: int64

In [49]:
data_train.fillna(0, inplace = True)

In [50]:
data_test['CPI'].fillna(data_test['CPI'].mean(), inplace = True)
data_test['Unemployment'].fillna(data_test['Unemployment'].mean(), inplace = True)

In [51]:
data_test.fillna(0, inplace = True)

In [52]:
data_train['IsHoliday'] = data_train['IsHoliday'].apply(lambda x: 1 if x == True else 0)
data_test['IsHoliday'] = data_test['IsHoliday'].apply(lambda x: 1 if x == True else 0)

In [53]:
data_train['Type'] = data_train['Type'].apply(lambda x: 1 if x == 'A' else (2 if x == 'B' else 3))
data_test['Type'] = data_test['Type'].apply(lambda x: 1 if x == 'A' else (2 if x == 'B' else 3))

In [54]:
features = [feature for feature in data_train.columns if feature not in ('Date','Weekly_Sales')]

In [55]:
X = data_train[features].copy()
y = data_train.Weekly_Sales.copy()

In [56]:
data_sample = data_train.copy().sample(frac=.25)
X_sample = data_sample[features].copy()
y_sample = data_sample.Weekly_Sales.copy()

In [57]:
X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_sample, y_sample, random_state=0, test_size=0.15)

In [58]:
feat_model = xgb.XGBRegressor(random_state=0).fit(X_train, y_train)

[13:55:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


In [59]:
!pip install eli5
import eli5
from eli5.sklearn import PermutationImportance

perm = PermutationImportance(feat_model, random_state=1).fit(X_valid, y_valid)
features = eli5.show_weights(perm, top=len(X_train.columns), feature_names = X_valid.columns.tolist())

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


[jovian] Detected Colab notebook...
[jovian] Please enter your API key ( from https://jovian.ai/ ):
API KEY: 

In [60]:
features_weights = eli5.show_weights(perm, top=len(X_train.columns), feature_names = X_valid.columns.tolist())
features_weights

In [61]:
f_importances = pd.Series(dict(zip(X_valid.columns.tolist(), perm.feature_importances_))).sort_values(ascending=False)
f_importances

Dept                     1.151494
Size                     0.344983
Store                    0.042446
CPI                      0.014942
Week                     0.012801
Type                     0.002686
Days_to_Thansksgiving    0.002074
Tranksgiving             0.001411
IsHoliday                0.001029
Unemployment             0.000616
MarkDown3                0.000383
Day                      0.000362
Fuel_Price               0.000270
Temperature              0.000212
MarkDown4                0.000052
Days_to_Christmas        0.000000
Christmas                0.000000
LaborDay                 0.000000
SuperBowlWeek            0.000000
MarkDown2                0.000000
Year                     0.000000
Month                    0.000000
MarkDown1                0.000000
MarkDown5                0.000000
MarkdownsSum             0.000000
dtype: float64

In [62]:
weights = eli5.show_weights(perm, top=len(X_train.columns), feature_names=X_valid.columns.tolist())
result = pd.read_html(weights.data)[0]
result

Weight                Feature
0   1.1515  ± 0.0269                   Dept
1   0.3450  ± 0.0144                   Size
2   0.0424  ± 0.0016                  Store
3   0.0149  ± 0.0011                    CPI
4   0.0128  ± 0.0017                   Week
5   0.0027  ± 0.0003                   Type
6   0.0021  ± 0.0002  Days_to_Thansksgiving
7   0.0014  ± 0.0017           Tranksgiving
8   0.0010  ± 0.0008              IsHoliday
9   0.0006  ± 0.0001           Unemployment
10  0.0004  ± 0.0004              MarkDown3
11  0.0004  ± 0.0000                    Day
12  0.0003  ± 0.0001             Fuel_Price
13  0.0002  ± 0.0002            Temperature
14  0.0001  ± 0.0000              MarkDown4
15       0  ± 0.0000              MarkDown1
16       0  ± 0.0000              MarkDown2
17       0  ± 0.0000              MarkDown5
18       0  ± 0.0000                   Year
19       0  ± 0.0000               LaborDay
20       0  ± 0.0000              Christmas
21       0  ± 0.0000          SuperBowlWeek
22       0  ± 0.0000      Days_to_Christmas
23       0  ± 0.0000                  Month
24       0  ± 0.0000           MarkdownsSum

# MODELLING

In [63]:
models = {
          '    LGBM': lgb.LGBMRegressor(random_state = 0),
          ' XGBoost': xgb.XGBRegressor(random_state = 0, objective = 'reg:squarederror'),
                    
          '    HGBR': HistGradientBoostingRegressor(random_state = 0),
          ' ExtraTr': ensemble.ExtraTreesRegressor(bootstrap = True, random_state = 0),
          ' RandomF': ensemble.RandomForestRegressor(random_state = 0),
         }

In [64]:
def model_evaluation (name, model, models, X_train, y_train, X_valid, y_valid):
   
    rmses = []
    
    for i in range(len(models)):
    
        # Model fit
        model.fit(X_train, y_train)
        
        # Model predict
        y_preds = model.predict(X_valid)

        # RMSE
        rmse = np.sqrt(np.mean((y_valid - y_preds)**2))
        rmses.append(rmse)
        
    return np.mean(rmses)

In [65]:
for name, model in models.items():
    print(name + ' Valid RMSE {:.4f}'.format(model_evaluation(name, model, models,  X_train, y_train, X_valid, y_valid)) )

    LGBM Valid RMSE 6919.3474
 XGBoost Valid RMSE 11584.0891
    HGBR Valid RMSE 6842.3784
 ExtraTr Valid RMSE 4867.1716
 RandomF Valid RMSE 4154.8841


**Seems to be RandomForest it's the best baseline model by default, followed by ExtraTrees, but you can improve the score of boosting models by doing hyperparameter optimization. Also, for a more generalizable model you can do a blend of the best models at the end.**

Stablish a baseline with the best model.

In [ ]:
X_baseline = X[['Store','Dept','IsHoliday','Size','Week','Type','Year','Day']].copy()
X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_baseline, y, random_state=0, test_size=0.1)
RF = ensemble.RandomForestRegressor(n_estimators=60, max_depth=25, min_samples_split=3, min_samples_leaf=1)
RF.fit(X_train, y_train)

RandomForestRegressor(max_depth=25, min_samples_split=3, n_estimators=60)

In [ ]:
test = data_test[['Store','Dept','IsHoliday','Size','Week','Type','Year','Day']].copy()
predict_rf = RF.predict(test)

In [ ]:
sample_submission['Weekly_Sales'] = predict_rf
sample_submission.to_csv('submission.csv',index=False)